In [1]:
using ModelingToolkit

$$ T_D (n, e_c) = J \frac{d^2 \theta_0 (t)}{dt^2} + B \frac{d \theta_0 (t)}{dt} $$

- $T_D$ : Torque Developed
- $J$ : Inertia
- $B$ : Dampening


Kim, et. al. 2011:

$$ \dot\theta = \omega$$
$$ \dot\omega = \frac{1}{J} ( -K_m i_a sin(N_r \theta) + K_m i_b cos(N_r \theta) - B \omega - \tau)$$
$$ \dot i_a = \frac{1}{L} ( v_a - R i_a + K_m sin(N_r \theta))$$
$$ \dot i_b = \frac{1}{L} ( v_b - R i_b - K_m cos(N_r \theta))$$


In [20]:
using ModelingToolkit, OrdinaryDiffEq, Unitful

@parameters t J Km Nr B τ R va vb L
@variables θ(t) ω(t) ia(t) ib(t)
D = Differential(t)

eqs = [D(θ) ~ ω,
       D(ω) ~ (1/J)*(-Km*ia*sin(Nr*θ) + Km*ib*cos(Nr*θ) - B*ω - τ),
       D(ia) ~ (1/L)*(va - R * ia + Km *ω*sin(Nr*θ)),
       D(ib) ~ (1/L)*(vb - R * ib - Km *ω*cos(Nr*θ))]

sys = ODESystem(eqs)
sys = ode_order_lowering(sys)

ODESystem(Equation[Equation(Differential(θ(t)), ω(t)), Equation(Differential(ω(t)), (1 / J) * ((((((-Km) * ia(t)) * sin(Nr * θ(t))) + ((Km * ib(t)) * cos(Nr * θ(t)))) - (B * ω(t))) - τ)), Equation(Differential(ia(t)), (1 / L) * ((va - (R * ia(t))) + ((Km * ω(t)) * sin(Nr * θ(t))))), Equation(Differential(ib(t)), (1 / L) * ((vb - (R * ib(t))) - ((Km * ω(t)) * cos(Nr * θ(t)))))], t, Term{Real}[θ(t), ω(t), ia(t), ib(t)], Sym{ModelingToolkit.Parameter{Real}}[Km, τ, J, Nr, B, L, R, va, vb], Num[], Equation[], Base.RefValue{Vector{Num}}(Num[]), Base.RefValue{Any}(Matrix{Num}(undef, 0, 0)), Base.RefValue{Matrix{Num}}(Matrix{Num}(undef, 0, 0)), Base.RefValue{Matrix{Num}}(Matrix{Num}(undef, 0, 0)), Symbol("##ODESystem#271"), ODESystem[])

In [32]:
u0 = [θ => 1.0,
      ω => 1.0,
      ia => 8.0,
      ib => 8.0]

p  = [J => 6.8e-5, # kg⋅m²
      Km => (0.44/1.68), # N⋅m/A
      Nr => 50.0,
      B => 0.001,
      va => 12,
      vb => 12,
      R  => 1.65,
      τ => 1.0,
      L => 2.8]

9-element Vector{Pair{Num, Float64}}:
  J => 6.8e-5
 Km => 0.2619047619047619
 Nr => 50.0
  B => 0.001
 va => 12.0
 vb => 12.0
  R => 1.65
  τ => 1.0
  L => 2.8

In [33]:
tspan = (0.0,1.0)
prob = ODEProblem(sys,u0,tspan,p)
@time sol = solve(prob,Tsit5())

  2.350369 seconds (2.71 M allocations: 145.556 MiB, 1.29% gc time, 99.94% compilation time)


retcode: Success
Interpolation: specialized 4th order "free" interpolation
t: 1355-element Vector{Float64}:
 0.0
 8.663057779366818e-5
 0.0002687335179147103
 0.0005262419410739111
 0.0008598882762382225
 0.0012760391598381892
 0.0017188402414794607
 0.0022722349661897837
 0.0027479945461831167
 0.0032756490177390284
 0.0038264742126059206
 0.004448486267669614
 0.005066119743779248
 ⋮
 0.9917982576512291
 0.9925094386584403
 0.9932980197931461
 0.9940474560832526
 0.9947555244789982
 0.9955447842006042
 0.9962898468273164
 0.9970017003921331
 0.9977907020614016
 0.9985393717145736
 0.9992480119621197
 1.0
u: 1355-element Vector{Vector{Float64}}:
 [1.0, 1.0, 8.0, 8.0]
 [1.0001730855846018, 2.9927961860856676, 7.999958693458025, 7.999947232925071]
 [1.0010925524160645, 7.0718967690754315, 7.99986073201632, 7.999785546098231]
 [1.0036047582404748, 12.29707926774481, 7.999715763510699, 7.999442980365503]
 [1.0086048221507415, 17.226957457543563, 7.999591379883451, 7.998834048070277]
 [1.0

In [34]:
using Plots; plotly(); plot(sol)

<!DOCTYPE html>
 
 
 Plots.jl